# Calibración de la cámara

La calibración de la cámara consiste en obtener la matriz de cámara $K$ a partir de un vídeo en el que se muestre una plantilla de referencia en diferentes posiciones respecto a la cámara.

Usaremos la plantilla tipo *tablero de ajedrez*, con 9x6 intersecciones claramente distinguibles.

In [48]:
import numpy as np
import cv2 as cv
import random
import math
import matplotlib.pyplot as plt

from IPython.display import display, clear_output
from ipywidgets import IntSlider, FloatSlider, Checkbox, interact, fixed


In [49]:
video_calibration = "../../../videos/calibration/calibration.mp4"


In [50]:
# Definición de la plantilla:
square_size = 1.0
pattern_size = (9, 6)
pattern_points = np.zeros((np.prod(pattern_size), 3), np.float32)
pattern_points[:, :2] = np.indices(pattern_size).T.reshape(-1, 2)
pattern_points *= square_size # pattern_points = array([[0., 0., 0.],[1., 0., 0.],...,[8., 0., 0.],[0., 1., 0.],...,[8., 5., 0.]], dtype=float32)

La función *process_video* encuentra las esquinas de la plantilla para algunos frames del vídeo *videofile*. Tiene 3 modos de uso:

* *'first'*: comportamiento anterior.
* *'random'*: selecciona *nframes* aleatorios del vídeo.
* *'equispaced'*: selecciona los frames del vídeo a intervalos equiespaciados de longitud $\lfloor\frac{N}{nframes}\rfloor$, con *N* el número total de frames del vídeo.

Los resultados se guardan en una lista de tuplas `(frame,points)`. Además hemos modificado la función para que no añada a los resultados los frames en los que no se detecten todas las esquinas de la plantilla (cuando la función *cv2.findChessBoardCorners* devuelve *found=0*). Esto lo hemos hecho para hacer una calibración más robusta y obtener una $K$ más precisa.

In [51]:
def get_fstep(videoreader, nframes):
# número de frames del vídeo
  nframes_total = int(videoreader.get(cv.CAP_PROP_FRAME_COUNT))
  fstep = nframes_total // nframes

  return nframes_total, fstep

PROCESS_VIDEO_MODES = {'first': 0, 'random': 1, 'equispaced': 2}

def process_video(videofile, nframes, mode='equispaced'):
  # Modificado para tomar muestras equiespaciadas en el tiempo

  # Puntos para el matching:
  obj_points = []
  img_points = []
  h, w = 0, 0

  # Apertura del archivo de vídeo:
  videoreader = cv.VideoCapture(videofile)

  # Seleccionar nframes equiespaciados:
  nframes_total, fstep = get_fstep(videoreader, nframes)

  if mode == 'equispaced':
    frames = range(0, nframes_total, fstep)
  elif mode == 'random':
    frames = random.sample(range(nframes_total), nframes)
  else:
    frames = np.arange(nframes)

  # Bucle principal de lectura de frames:
  i, j, ntempl, results = 0, 0, 0, []

  for i in range(nframes_total):

    (grabbed, img) = videoreader.read()
    if grabbed and i in frames:
      imggray = cv.cvtColor(img, cv.COLOR_BGR2GRAY)
      rows, cols = imggray.shape[:2]

      # Imagen para dibujar después las esquinas detectadas:
      vis = cv.cvtColor(img, cv.COLOR_BGR2RGB)

      # Encontrar y dibujar esquinas detectadas:
      flags = (cv.CALIB_CB_ADAPTIVE_THRESH + cv.CALIB_CB_NORMALIZE_IMAGE +
               cv.CALIB_CB_FAST_CHECK)
      found, corners = cv.findChessboardCorners(imggray, pattern_size, flags=flags)
      if found:
        ntempl += 1
        term = (cv.TERM_CRITERIA_EPS+cv.TERM_CRITERIA_COUNT, 30, 0.1)
        cv.cornerSubPix(imggray, corners, (5, 5), (-1, -1), term)
        cv.drawChessboardCorners(vis, pattern_size, corners, found)
        msg = "({0}/{1}) detected/input frames".format(ntempl, j+1)
        clear_output(wait=True)
        display(msg)
        results.append((vis, corners))
      j += 1
    # Siguiente frame:

  # Cerrar el vídeo
  videoreader.release()
  # Devolvemos todos los resultados del procesamiento frame a frame:
  return results

In [52]:
from IPython.display import HTML
from base64 import b64encode

def play_video(videofilename):
    mp4 = open(videofilename,'rb').read()
    data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
    return HTML("""
    <video width=400 controls>
      <source src="%s" type="video/mp4">
    </video>
    """ % data_url)

def extract_frame(video, framepos):
  videoreader = cv.VideoCapture(video)

  while True:
    (grabbed, frame) = videoreader.read()
    if not grabbed:
      break
    if framepos == 0:
      break
    framepos -= 1
  videoreader.release()
  return frame

In [53]:
play_video(video_calibration)

Ahora se procesa el vídeo para detectar las esquinas de la plantilla. La resolución del vídeo es de 1920 x 1080 y se tratan de detectar las  54=9×6  esquinas en cada frame seleccionado. Hemos decidido muestrear 200 frames aleatorios del vídeo para la calibración. En 194 de ellos la plantilla se detectó correctamente.

In [54]:
results = process_video(video_calibration, 1500, mode='random')
print("Forma del array de la primera imagen: ", results[0][0].shape)
print("Forma del array de la primera lista de puntos: ", results[0][1].shape)

'(72/1346) detected/input frames'

Forma del array de la primera imagen:  (720, 1280, 3)
Forma del array de la primera lista de puntos:  (54, 1, 2)


A continuación podemos ver para cada frame seleccionado las esquinas detectadas. Cada una de las 6 filas de la plantilla tiene un color en la imagen y se une con una línea la última celda de cada fila (a un lado) con la primera de la siguiente (al otro) para que podamos comprobar con este orden que la correspondencia con la plantilla es buena.

In [55]:
def plot_image(results, framepos):
  inimg, _ = results[framepos]
  fig, axes = plt.subplots(1,1,figsize=(8.,16.))
  axes.imshow(inimg, cmap='gray')
  plt.show()

In [ ]:
interact(plot_image,
         results=fixed(results),
         framepos=IntSlider(value=0, min=0, max=len(results)-1, orientation='horizontal', continuous_update=False)
         );

interactive(children=(IntSlider(value=0, continuous_update=False, description='framepos', max=71), Output()), …

Comprobamos resultados, y elaboramos lista de puntos correspondientes (_matchings_) para cada frame, éstos últimos prefijados con las coordenadas canónicas de los puntos en la plantilla (nótese que el algoritmo de extracción extrae las coordenadas con precisión [_subpixel_](https://docs.opencv.org/master/dd/d1a/group__imgproc__feature.html#ga354e0d7c86d0d9da75de9b9701a9a87e) ):

In [57]:
img_points0 = [elem[1] for elem in results if elem[1] is not None]
obj_points = [pattern_points for elem in img_points0]
print(img_points0[0][:9]) # Imprimimos última fila (en la imagen; es la primera fila en el array) de esquinas del primer frame.
print(img_points0[0].shape)
print(obj_points[0][:9]) # Idem para las coordenadas canónicas de la plantilla.
print(obj_points[0].shape)

[[[413.9214  359.3521 ]]

 [[410.84653 368.42868]]

 [[407.5259  377.58527]]

 [[404.60205 387.30255]]

 [[401.18433 396.08377]]

 [[397.7193  405.33676]]

 [[394.69962 414.64816]]

 [[391.62402 423.51038]]

 [[388.34293 432.65735]]]
(54, 1, 2)
[[0. 0. 0.]
 [1. 0. 0.]
 [2. 0. 0.]
 [3. 0. 0.]
 [4. 0. 0.]
 [5. 0. 0.]
 [6. 0. 0.]
 [7. 0. 0.]
 [8. 0. 0.]]
(54, 3)


Con los puntos extraídos de 100 frames aleatorios calculamos la matriz de cámara y los parámetros de la distorsión radial con el método `cv2.calibrateCamera()` de *OpenCV*. El valor de RMSE nos da una idea del error de reproyección de los puntos con la calibración empleada. En nuestro caso tenemos RMSE=0.85, mayor que el ejemplo de clase (0.28) por lo que se espera una mayor imprecisión al detectar la pose de la cámara usando el marcador RA.

In [58]:
calibframes = min(500, img_points0.__len__())
obj_points = [pattern_points for i in range(calibframes)]
img_points = random.sample(img_points0, calibframes)

print("Calibrating for ({0}/{1}) randomly selected images...".format(calibframes, len(results)))
rows, cols = results[0][0].shape[:2]
rmse, camera_matrix, dist_coefs, rvecs, tvecs = cv.calibrateCamera(obj_points, img_points, (rows, cols), None, None)
print("RMSE:", rmse)
print("Camera matrix:\n", camera_matrix)
print("Distortion coefficients: ", dist_coefs.ravel())

Calibrating for (72/72) randomly selected images...
RMSE: 0.311467056466509
Camera matrix:
 [[1.33888047e+03 0.00000000e+00 3.56588343e+02]
 [0.00000000e+00 1.30104316e+03 6.44069761e+02]
 [0.00000000e+00 0.00000000e+00 1.00000000e+00]]
Distortion coefficients:  [ 7.84968048e-01 -4.38034367e+01 -5.00022009e-02 -3.42284994e-02
  4.38908717e+02]


La matriz de cámara siempre es triangular superior con $K_{3 3} = 1$. En nuestro caso no hay *skew* ($s=0$) y $K_{1 1} = f \approx fr = K_{2 2}$ lo que parece razonable para la configuración de cámara del móvil escogida. El centro óptico es aproximadamente $(680, 916)$. Los coeficientes de distorsión tienen valor absoluto menor que 1.

$f_x$ y $f_y$ nos dan los ángulos de _field of view_ horizontal y vertical de nuestra cámara:

In [59]:
print("fov h: {0:.1f}º, fov v: {1:.1f}º".format(
  math.degrees(2*math.atan2(cols/2, camera_matrix[0][0])),
  math.degrees(2*math.atan2(rows/2, camera_matrix[1][1]))))

fov h: 51.1º, fov v: 30.9º
